## Introduction/Buisness Problem

A resturant is to be opened in a borough of New York. For this problem Brooklyn, NY is selected. The neighbourhood in which the resturant should be opened is to be decided.The deciding factor in selection is the proximity to other popular resturants. Foursquare api is used to get the location data of the top venues in each neighbourhood. The neighbourhoods with least number of resturants are examined for deciding the final location.

## Table of Contents


<font size = 3>

1.  Methodology

2.  Explore Brooklyn

3.  Analyze Each Neighborhood

4.  Cluster Neighborhoods

5.  Examine Clusters 

6.  Conclusion
    </font>
    </div>


Importing libraries


In [1]:
%matplotlib inline
import matplotlib.pyplot
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans


import folium # map rendering library

print('Libraries imported.')

Libraries imported.


<a id='item1'></a>


## 1. Methodology


New York has a total of 5 boroughs and 306 neighborhoods. In order to segement the neighborhoods and explore them, we will essentially need a dataset that contains the 5 boroughs and the neighborhoods that exist in each borough as well as the the latitude and logitude coordinates of each neighborhood.New York data can be downloaded from:

https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json


#### Load and explore the data


Next, let's load the data.


In [2]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [3]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [4]:
neighborhoods_data = newyork_data['features']

Let's take a look at the first item in this list.


In [5]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

#### Transforming to dataframe


In [6]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [7]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [8]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [9]:
neighborhoods.head(10)

Borough    Neighborhood   Latitude  Longitude
0      Bronx       Wakefield  40.894705 -73.847201
1      Bronx      Co-op City  40.874294 -73.829939
2      Bronx     Eastchester  40.887556 -73.827806
3      Bronx       Fieldston  40.895437 -73.905643
4      Bronx       Riverdale  40.890834 -73.912585
5      Bronx     Kingsbridge  40.881687 -73.902818
6  Manhattan     Marble Hill  40.876551 -73.910660
7      Bronx        Woodlawn  40.898273 -73.867315
8      Bronx         Norwood  40.877224 -73.879391
9      Bronx  Williamsbridge  40.881039 -73.857446

And make sure that the dataset has all 5 boroughs and 306 neighborhoods.


In [10]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


#### Use geopy library to get the latitude and longitude values of New York City.


In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>ny_explorer</em>, as shown below.


In [11]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


#### Create a map of New York with neighborhoods superimposed on top.


In [12]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

We will now cluster only the neighborhoods in Brooklyn. So let's slice the original dataframe and create a new dataframe of the Brooklyn data.


In [13]:
brooklyn_data = neighborhoods[neighborhoods['Borough'] == 'Brooklyn'].reset_index(drop=True)
brooklyn_data.head()

Borough Neighborhood   Latitude  Longitude
0  Brooklyn    Bay Ridge  40.625801 -74.030621
1  Brooklyn  Bensonhurst  40.611009 -73.995180
2  Brooklyn  Sunset Park  40.645103 -74.010316
3  Brooklyn   Greenpoint  40.730201 -73.954241
4  Brooklyn    Gravesend  40.595260 -73.973471

Let's get the geographical coordinates of Manhattan.


In [14]:
address = 'Brooklyn, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Brooklyn are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Brooklyn are 40.6501038, -73.9495823.


Visualization of Brooklyn and the neighborhoods in it.


In [15]:
# create map of Brooklyn using latitude and longitude values
map_brooklyn = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(brooklyn_data['Latitude'], brooklyn_data['Longitude'], brooklyn_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_brooklyn)  
    
map_brooklyn

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.


#### Define Foursquare Credentials and Version


In [27]:
# @hidden_cell
#CLIENT_ID = '****' # your Foursquare ID(hidden)
#CLIENT_SECRET = '****' # your Foursquare Secret(hidden)
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value
#ACCESSS_TOKEN='****'#(hidden)

print('Credentials established:')


Credentials established:


#### Let's explore the first neighborhood in our dataframe.


Get the neighborhood's name.


In [30]:
brooklyn_data.loc[0, 'Neighborhood']

'Bay Ridge'

Get the neighborhood's latitude and longitude values.


In [31]:
neighborhood_latitude = brooklyn_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = brooklyn_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = brooklyn_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Bay Ridge are 40.625801065010656, -74.03062069353813.


#### Top 100 venues that are in Bay Ridge within a radius of 1000 meters.


In [32]:


url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    1000, 
    LIMIT)

In [35]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5ff52a992e06dd09d5667cf5'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'},
    {'name': '$-$$$$', 'key': 'price'}]},
  'headerLocation': 'Bay Ridge',
  'headerFullLocation': 'Bay Ridge, Brooklyn',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 178,
  'suggestedBounds': {'ne': {'lat': 40.63480107401067,
    'lng': -74.01878477359382},
   'sw': {'lat': 40.616801056010644, 'lng': -74.04245661348243}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b895827f964a5206c2d32e3',
       'name': 'Pilo Arts Day Spa and Salon',
       'location': {'address': '8412 3rd Ave',
        'lat': 40.62474788273414,
        'lng': -74.03059056940135,
        'labeledLa

In [36]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a _pandas_ dataframe.


In [37]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

<ipython-input-37-561c05f0fdd1>:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  nearby_venues = json_normalize(venues) # flatten JSON


name      categories        lat        lng
0  Pilo Arts Day Spa and Salon             Spa  40.624748 -74.030591
1                    Bagel Boy      Bagel Shop  40.627896 -74.029335
2                 Pegasus Cafe  Breakfast Spot  40.623168 -74.031186
3          Ho' Brah Taco Joint      Taco Place  40.622960 -74.031371
4                   Mimi Nails             Spa  40.622571 -74.031477

In [38]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


<a id='item2'></a>


## 2. Explore Neighborhoods in Brooklyn


Function for getting top 100 venues for all neighbourhoods in Brooklyn

In [39]:
def getNearbyVenues(names, latitudes, longitudes, radius=1000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            100)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called _brooklyn_venues_.


In [40]:
brooklyn_venues = getNearbyVenues(names=brooklyn_data['Neighborhood'],
                                   latitudes=brooklyn_data['Latitude'],
                                   longitudes=brooklyn_data['Longitude']
                                  )


Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Ditmas Park
Wingate
Rugby
Remsen Village
New Lots
Paerdegat Basin
Mill Basin
Fulton Ferry
Vinegar Hill
Weeksville
Broadway Junction
Dumbo
Homecrest
Highland Park
Madison
Erasmus


#### Let's check the size of the resulting dataframe


In [41]:
print(brooklyn_venues.shape)
brooklyn_venues.head(100)
brooklyn_venues.to_csv('brooklyn_venues.csv')

(5634, 7)


In [42]:
brooklyn_venues.groupby('Neighborhood').count()
brooklyn_venues

Neighborhood  Neighborhood Latitude  \
0                     Bay Ridge              40.625801   
1                     Bay Ridge              40.625801   
2                     Bay Ridge              40.625801   
3                     Bay Ridge              40.625801   
4                     Bay Ridge              40.625801   
5                     Bay Ridge              40.625801   
6                     Bay Ridge              40.625801   
7                     Bay Ridge              40.625801   
8                     Bay Ridge              40.625801   
9                     Bay Ridge              40.625801   
10                    Bay Ridge              40.625801   
11                    Bay Ridge              40.625801   
12                    Bay Ridge              40.625801   
13                    Bay Ridge              40.625801   
14                    Bay Ridge              40.625801   
15                    Bay Ridge              40.625801   
16                    Bay Ridge              40.625801   
17                    Bay Ridge              40.625801   
18                    Bay Ridge              40.625801   
19                    Bay Ridge              40.625801   
20                    Bay Ridge              40.625801   
21                    Bay Ridge              40.625801   
22                    Bay Ridge              40.625801   
23                    Bay Ridge              40.625801   
24                    Bay Ridge              40.625801   
25                    Bay Ridge              40.625801   
26                    Bay Ridge              40.625801   
27                    Bay Ridge              40.625801   
28                    Bay Ridge              40.625801   
29                    Bay Ridge              40.625801   
30                    Bay Ridge              40.625801   
31                    Bay Ridge              40.625801   
32                    Bay Ridge              40.625801   
33                    Bay Ridge              40.625801   
34                    Bay Ridge              40.625801   
35                    Bay Ridge              40.625801   
36                    Bay Ridge              40.625801   
37                    Bay Ridge              40.625801   
38                    Bay Ridge              40.625801   
39                    Bay Ridge              40.625801   
40                    Bay Ridge              40.625801   
41                    Bay Ridge              40.625801   
42                    Bay Ridge              40.625801   
43                    Bay Ridge              40.625801   
44                    Bay Ridge              40.625801   
45                    Bay Ridge              40.625801   
46                    Bay Ridge              40.625801   
47                    Bay Ridge              40.625801   
48                    Bay Ridge              40.625801   
49                    Bay Ridge              40.625801   
50                    Bay Ridge              40.625801   
51                    Bay Ridge              40.625801   
52                    Bay Ridge              40.625801   
53                    Bay Ridge              40.625801   
54                    Bay Ridge              40.625801   
55                    Bay Ridge              40.625801   
56                    Bay Ridge              40.625801   
57                    Bay Ridge              40.625801   
58                    Bay Ridge              40.625801   
59                    Bay Ridge              40.625801   
60                    Bay Ridge              40.625801   
61                    Bay Ridge              40.625801   
62                    Bay Ridge              40.625801   
63                    Bay Ridge              40.625801   
64                    Bay Ridge              40.625801   
65                    Bay Ridge              40.625801   
66                    Bay Ridge              40.625801   
67                    Bay Ridge              40.625801   
68               

#### Let's find out how many unique categories can be curated from all the returned venues


In [44]:
print('There are {} uniques categories.'.format(len(brooklyn_venues['Venue Category'].unique())))


There are 349 uniques categories.


<a id='item3'></a>


## 3. Analyze Each Neighborhood


In [45]:
# one hot encoding
brooklyn_onehot = pd.get_dummies(brooklyn_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
brooklyn_onehot['Neighborhood'] = brooklyn_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [brooklyn_onehot.columns[-1]] + list(brooklyn_onehot.columns[:-1])
brooklyn_onehot = brooklyn_onehot[fixed_columns]

brooklyn_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  African Restaurant  \
0            0                  0               0                   0   
1            0                  0               0                   0   
2            0                  0               0                   0   
3            0                  0               0                   0   
4            0                  0               0                   0   

   American Restaurant  Amphitheater  Animal Shelter  Antique Shop  Aquarium  \
0                    0             0               0             0         0   
1                    0             0               0             0         0   
2                    0             0               0             0         0   
3                    0             0               0             0         0   
4                    0             0               0             0         0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Austrian Restaurant  BBQ Joint  Bagel Shop  \
0                   0                    0          0           0   
1                   0                    0          0           1   
2                   0                    0          0           0   
3                   0                    0          0           0   
4                   0                    0          0           0   

   Baggage Locker  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0               0       0     0    0               0                 0   
1               0       0     0    0               0                 0   
2               0       0     0    0               0                 0   
3               0       0     0    0               0                 0   
4               0       0     0    0               0                 0   

   Basketball Court  Basketball Stadium  Bath House  Beach  Bed & Breakfast  \
0                 0                   0           0      0                0   
1                 0                   0           0      0                0   
2                 0                   0           0      0                0   
3                 0                   0           0      0                0   
4                 0                   0           0      0                0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0         0            0           0              0                         0   
1         0            0           0              0                         0   
2         0            0           0              0                         0   
3         0            0           0              0                         0   
4         0            0           0              0                         0   

   Bike Shop  Bike Trail  Bistro  Board Shop  Boat or Ferry  Bookstore  \
0          0           0       0           0              0          0   
1          0           0       0           0              0          0   
2          0           0       0           0              0          0   
3          0           0       0           0              0          0   
4          0 

And let's examine the new dataframe size.


In [46]:
brooklyn_onehot.shape

(5634, 349)

#### Grouping rows by neighborhood and by taking the mean of the frequency of occurrence of each category


In [90]:
brooklyn_grouped = brooklyn_onehot.groupby('Neighborhood').mean().reset_index()
brooklyn_grouped

Neighborhood  Yoga Studio  Accessories Store  Adult Boutique  \
0                  Bath Beach     0.000000           0.000000            0.00   
1                   Bay Ridge     0.010000           0.000000            0.00   
2          Bedford Stuyvesant     0.010000           0.000000            0.00   
3                 Bensonhurst     0.000000           0.000000            0.00   
4                Bergen Beach     0.000000           0.000000            0.00   
5                 Boerum Hill     0.020000           0.000000            0.00   
6                Borough Park     0.000000           0.000000            0.00   
7              Brighton Beach     0.000000           0.000000            0.00   
8           Broadway Junction     0.000000           0.000000            0.00   
9            Brooklyn Heights     0.050000           0.000000            0.00   
10                Brownsville     0.000000           0.000000            0.00   
11                   Bushwick     0.020000           0.000000            0.00   
12                   Canarsie     0.000000           0.000000            0.00   
13            Carroll Gardens     0.030000           0.000000            0.00   
14                  City Line     0.015152           0.000000            0.00   
15               Clinton Hill     0.040000           0.000000            0.00   
16                Cobble Hill     0.040000           0.000000            0.00   
17               Coney Island     0.000000           0.000000            0.00   
18              Crown Heights     0.010000           0.000000            0.00   
19              Cypress Hills     0.000000           0.000000            0.00   
20                Ditmas Park     0.010000           0.000000            0.00   
21                   Downtown     0.020000           0.000000            0.00   
22                      Dumbo     0.020000           0.000000            0.00   
23              Dyker Heights     0.010638           0.000000            0.00   
24              East Flatbush     0.000000           0.000000            0.00   
25              East New York     0.038462           0.000000            0.00   
26          East Williamsburg     0.010000           0.000000            0.00   
27                    Erasmus     0.010417           0.000000            0.00   
28                   Flatbush     0.010000           0.000000            0.00   
29                  Flatlands     0.000000           0.000000            0.00   
30                Fort Greene     0.010000           0.000000            0.00   
31              Fort Hamilton     0.000000           0.000000            0.00   
32               Fulton Ferry     0.020000           0.000000            0.00   
33                 Georgetown     0.000000           0.000000            0.00   
34            Gerritsen Beach     0.000000           0.000000            0.00   
35                    Gowanus     0.010000           0.000000            0.00   
36                  Gravesend     0.000000           0.000000            0.00   
37                 Greenpoint     0.040000           0.000000            0.00   
38              Highland Park     0.000000           0.000000            0.00   
39                  Homecrest     0.000000           0.000000            0.00   
40                 Kensington     0.010000           0.000000            0.00   
41                    Madison     0.000000           0.000000            0.00   
42            Manhattan Beach     0.017241           0.000000            0.00   
43          Manhattan Terrace     0.000000           0.000000            0.00   
44                Marine Park     0.000000           0.020000            0.00   
45                    Midwood     0.000000           0.000000            0.00   
46                 Mill Basin     0.000000           0.020619            0.00   
47                Mill Island     0.000000           0.000000            0.00   
48                   New Lots     0.000000      

In [91]:
brooklyn_grouped.shape

(70, 349)

In [92]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 5 venues for each neighborhood.


In [93]:
num_top_venues = 5

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = brooklyn_grouped['Neighborhood']

for ind in np.arange(brooklyn_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(brooklyn_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Bath Beach           Pizza Place   Japanese Restaurant   
1           Bay Ridge                   Spa           Pizza Place   
2  Bedford Stuyvesant           Coffee Shop           Pizza Place   
3         Bensonhurst                  Bank              Pharmacy   
4        Bergen Beach    Italian Restaurant         Deli / Bodega   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
0    Chinese Restaurant                  Bank  Cantonese Restaurant  
1    Italian Restaurant                   Bar    Chinese Restaurant  
2                   Bar                  Café             Wine Shop  
3                Bakery    Chinese Restaurant           Pizza Place  
4               Stables   American Restaurant           Supermarket

In [94]:
num_top_venues = 20
arr=[]

for hood in brooklyn_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = brooklyn_grouped[brooklyn_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    temp.head()
    print('\n')
print(temp)


----Bath Beach----
                    venue  freq
0             Pizza Place  0.08
1     Japanese Restaurant  0.05
2                    Bank  0.05
3      Chinese Restaurant  0.05
4                  Bakery  0.04
5    Cantonese Restaurant  0.04
6         Bubble Tea Shop  0.03
7        Sushi Restaurant  0.03
8             Coffee Shop  0.03
9      Italian Restaurant  0.03
10        Supplement Shop  0.02
11             Kids Store  0.02
12                  Diner  0.02
13             Donut Shop  0.02
14      Mobile Phone Shop  0.02
15                   Park  0.02
16           Dessert Shop  0.02
17           Gourmet Shop  0.02
18       Asian Restaurant  0.02
19  Vietnamese Restaurant  0.02


----Bay Ridge----
                        venue  freq
0                 Pizza Place  0.07
1                         Spa  0.07
2          Italian Restaurant  0.06
3          Chinese Restaurant  0.04
4                         Bar  0.04
5         American Restaurant  0.03
6              Cosmetics Shop  0.03
7

In [95]:
temp['venue']
temp['freq']
temp.head(5)

venue  freq
1          Yoga Studio   0.0
2    Accessories Store   0.0
3       Adult Boutique   0.0
4   African Restaurant   0.0
5  American Restaurant   0.0

<a id='item4'></a>


In [96]:

data = brooklyn_venues['Venue Category'].value_counts().to_dict()
sr=pd.DataFrame.from_dict(data,orient='index')
sr

0
Pizza Place                               296
Coffee Shop                               181
Bar                                       158
Bakery                                    139
Grocery Store                             130
Caribbean Restaurant                      128
Italian Restaurant                        111
Chinese Restaurant                        103
Café                                      102
Donut Shop                                 95
Deli / Bodega                              95
Bank                                       94
Ice Cream Shop                             94
Park                                       93
Sandwich Place                             88
Mexican Restaurant                         86
Pharmacy                                   86
Bagel Shop                                 85
American Restaurant                        76
Cocktail Bar                               76
Supermarket                                73
Wine Shop                                  71
Discount Store                             69
Japanese Restaurant                        65
Yoga Studio                                65
Mobile Phone Shop                          64
Gym                                        63
Fast Food Restaurant                       58
Playground                                 58
Sushi Restaurant                           55
Restaurant                                 54
Gym / Fitness Center                       54
Fried Chicken Joint                        53
Cosmetics Shop                             47
Diner                                      46
Spa                                        45
Seafood Restaurant                         43
Burger Joint                               41
Liquor Store                               41
Latin American Restaurant                  40
Thai Restaurant                            39
Middle Eastern Restaurant                  38
Convenience Store                          35
Wine Bar                                   34
Bookstore                                  30
Department Store                           29
Furniture / Home Store                     29
Bus Station                                29
Food Truck                                 28
Gourmet Shop                               28
Breakfast Spot                             28
Lounge                                     28
Clothing Store                             27
Juice Bar                                  26
Vietnamese Restaurant                      26
Scenic Lookout                             26
Indian Restaurant                          25
Video Game Store                           25
French Restaurant                          24
Gas Station                                24
Art Gallery                                23
Vegetarian / Vegan Restaurant              22
Southern / Soul Food Restaurant            22
Pet Store                                  21
Dessert Shop                               20
Kids Store                                 20
Farmers Market                             20
Gift Shop                                  20
Performing Arts Venue                      20
Sporting Goods Shop                        20
New American Restaurant                    20
Theme Park Ride / Attraction               19
Taco Place                                 19
Beach                                      19
Russian Restaurant                         19
Brewery                                    18
Theater                                    17
Music Venue                                17
Supplement Shop                            17
Plaza                                      17
Turkish Restaurant                         17
Flower Shop                                17
Asian Restaurant                           17
Beer Garden                                16
Mediterranean Restaurant                   16
Food & Drink Shop                          15
Hotel                                     

From the abve table it is clear that the most popular places are pizza shops and coffee shops

## 4. Cluster Neighborhoods


Run _k_-means to cluster the neighborhood into 8 clusters.


In [97]:
# set number of clusters
kclusters = 8

brooklyn_grouped_clustering = brooklyn_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(brooklyn_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 2, 2, 1, 5, 2, 1, 1, 1, 3])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.


In [98]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

brooklyn_merged = brooklyn_data


brooklyn_merged = brooklyn_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

brooklyn_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Brooklyn    Bay Ridge  40.625801 -74.030621               2   
1  Brooklyn  Bensonhurst  40.611009 -73.995180               1   
2  Brooklyn  Sunset Park  40.645103 -74.010316               1   
3  Brooklyn   Greenpoint  40.730201 -73.954241               2   
4  Brooklyn    Gravesend  40.595260 -73.973471               1   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                   Spa           Pizza Place    Italian Restaurant   
1                  Bank              Pharmacy                Bakery   
2                Bakery    Mexican Restaurant           Pizza Place   
3           Coffee Shop                   Bar          Cocktail Bar   
4            Donut Shop           Pizza Place                Bakery   

  4th Most Common Venue  5th Most Common Venue  
0                   Bar     Chinese Restaurant  
1    Chinese Restaurant            Pizza Place  
2                  Bank  Vietnamese Restaurant  
3           Yoga Studio            Pizza Place  
4              Pharmacy                   Park

Finally, let's visualize the resulting clusters


In [102]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(brooklyn_merged['Latitude'], brooklyn_merged['Longitude'], brooklyn_merged['Neighborhood'], brooklyn_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=20,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.3).add_to(map_clusters)
       
map_clusters

<a id='item5'></a>


## 5. Examine Clusters


We can now examine each cluster and determine cluster and neighbourhood which does not have resturants as the most popular venue. Based on that we can determine the location for opening a resturant.


#### Cluster 1


In [104]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 0, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
8                    Flatbush           Pizza Place  Caribbean Restaurant   
10              East Flatbush  Caribbean Restaurant        Discount Store   
28                   Canarsie  Caribbean Restaurant           Pizza Place   
29                  Flatlands  Caribbean Restaurant                  Park   
42  Prospect Lefferts Gardens  Caribbean Restaurant           Pizza Place   
47        Prospect Park South  Caribbean Restaurant           Pizza Place   
54                Ditmas Park  Caribbean Restaurant    Mexican Restaurant   
55                    Wingate  Caribbean Restaurant         Grocery Store   
56                      Rugby  Caribbean Restaurant           Pizza Place   
57             Remsen Village  Caribbean Restaurant    Chinese Restaurant   
59            Paerdegat Basin  Caribbean Restaurant         Grocery Store   
63                 Weeksville        Discount Store         Grocery Store   
69                    Erasmus  Caribbean Restaurant        Discount Store   

   3rd Most Common Venue            4th Most Common Venue  \
8            Coffee Shop               Mexican Restaurant   
10           Supermarket                           Lounge   
28                  Bank                    Grocery Store   
29        Discount Store                      Supermarket   
42                  Café                           Bakery   
47    Mexican Restaurant                      Coffee Shop   
54           Pizza Place                      Coffee Shop   
55           Pizza Place                   Sandwich Place   
56              Pharmacy                       Donut Shop   
57           Bus Station             Fast Food Restaurant   
59       Harbor / Marina                      Pizza Place   
63    Chinese Restaurant  Southern / Soul Food Restaurant   
69    Chinese Restaurant                    Deli / Bodega   

   5th Most Common Venue  
8                    Bar  
10           Bus Station  
28            Bagel Shop  
29              Pharmacy  
42             Wine Shop  
47         Grocery Store  
54     Mobile Phone Shop  
55   Fried Chicken Joint  
56     Mobile Phone Shop  
57            Donut Shop  
59    Athletics & Sports  
63  Fast Food Restaurant  
69           Pizza Place

#### Cluster 2


In [105]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 1, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
1         Bensonhurst                  Bank              Pharmacy   
2         Sunset Park                Bakery    Mexican Restaurant   
4           Gravesend            Donut Shop           Pizza Place   
5      Brighton Beach                Bakery                 Beach   
6      Sheepshead Bay    Italian Restaurant      Sushi Restaurant   
7   Manhattan Terrace           Pizza Place                  Bank   
9       Crown Heights                  Café           Pizza Place   
11         Kensington           Pizza Place         Grocery Store   
27      Starrett City      Department Store           Pizza Place   
33         Bath Beach           Pizza Place   Japanese Restaurant   
34       Borough Park           Pizza Place                  Bank   
35      Dyker Heights           Pizza Place    Chinese Restaurant   
36    Gerritsen Beach            Donut Shop           Pizza Place   
37        Marine Park        Clothing Store        Cosmetics Shop   
43         Ocean Hill        Discount Store   Fried Chicken Joint   
46            Midwood           Pizza Place                  Café   
48         Georgetown                  Bank    Italian Restaurant   
52      Ocean Parkway            Donut Shop                  Bank   
53      Fort Hamilton           Pizza Place   Japanese Restaurant   
60         Mill Basin        Clothing Store           Pizza Place   
64  Broadway Junction         Deli / Bodega        Discount Store   
66          Homecrest                  Bank         Grocery Store   
68            Madison           Pizza Place      Sushi Restaurant   

              3rd Most Common Venue   4th Most Common Venue  \
1                            Bakery      Chinese Restaurant   
2                       Pizza Place                    Bank   
4                            Bakery                Pharmacy   
5                        Restaurant      Russian Restaurant   
6                Russian Restaurant      Turkish Restaurant   
7                  Sushi Restaurant              Donut Shop   
9   Southern / Soul Food Restaurant    Caribbean Restaurant   
11                    Deli / Bodega         Thai Restaurant   
27                Mobile Phone Shop  Furniture / Home Store   
33               Chinese Restaurant                    Bank   
34                           Bakery                Pharmacy   
35                       Bagel Shop    Gym / Fitness Center   
36                   Ice Cream Shop      Seafood Restaurant   
37                   Sandwich Place  Furniture / Home Store   
43                             Café             Pizza Place   
46                   Ice Cream Shop        Sushi Restaurant   
48               Chinese Restaurant           Deli / Bodega   
52               Italian Restaurant           Grocery Store   
53                              Bar              Bagel Shop   
60               Italian Restaurant                Pharmacy   
64                   Sandwich Place              Donut Shop   
66                         Pharmacy              Donut Shop   
68                       Bagel Shop                Pharmacy   

              5th Most Common Venue  
1                       Pizza Place  
2             Vietnamese Restaurant  
4                              Park  
5                              Bank  
6                              Café  
7                        Bagel Shop  
9                     Grocery Store  
11                      Gas Station  
27                         Pharmacy  
33             Cantonese Restaurant  
34                   Sandwich Place  
35                   Cosmetics Shop  
36                  Harbor / Marina  
37              American Restaurant  
43  Southern / Soul Food Restaurant  
46                             Bank  
48                      Supermarket  
52                 Sushi Restaurant  
53             Gym / Fitness Center  
60                             Bank  
64                      Pizza Place  
66 

#### Cluster 3


In [106]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 2, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0            Bay Ridge                   Spa           Pizza Place   
3           Greenpoint           Coffee Shop                   Bar   
13    Prospect Heights                   Bar    Mexican Restaurant   
15        Williamsburg                   Bar           Pizza Place   
16            Bushwick                   Bar           Coffee Shop   
17  Bedford Stuyvesant           Coffee Shop           Pizza Place   
19         Cobble Hill    Italian Restaurant          Cocktail Bar   
20     Carroll Gardens           Coffee Shop    Italian Restaurant   
22             Gowanus                   Bar           Coffee Shop   
23         Fort Greene    Italian Restaurant          Cocktail Bar   
24          Park Slope           Coffee Shop                   Spa   
38        Clinton Hill    Italian Restaurant           Pizza Place   
40            Downtown           Coffee Shop                   Bar   
41         Boerum Hill                   Bar           Coffee Shop   
49   East Williamsburg                   Bar           Coffee Shop   
50          North Side           Coffee Shop           Pizza Place   
51          South Side           Pizza Place                   Bar   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
0     Italian Restaurant                   Bar    Chinese Restaurant  
3           Cocktail Bar           Yoga Studio           Pizza Place  
13          Cocktail Bar             Wine Shop           Yoga Studio  
15           Coffee Shop   American Restaurant              Wine Bar  
16    Mexican Restaurant          Cocktail Bar         Deli / Bodega  
17                   Bar                  Café             Wine Shop  
19           Pizza Place                Bakery                   Bar  
20                Bakery                   Bar                   Spa  
22    Italian Restaurant             Wine Shop           Pizza Place  
23           Pizza Place           Coffee Shop            Playground  
24           Pizza Place             Gift Shop            Bagel Shop  
38             Wine Shop           Coffee Shop           Yoga Studio  
40                Bakery          Burger Joint         Grocery Store  
41         Grocery Store     French Restaurant                Bakery  
49          Cocktail Bar                Bakery    Italian Restaurant  
50              Wine Bar                Bakery           Yoga Studio  
51           Coffee Shop              Wine Bar   American Restaurant

#### Cluster 4


In [107]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 3, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
12   Windsor Terrace    Italian Restaurant                  Café   
18  Brooklyn Heights                  Park           Yoga Studio   
21          Red Hook                  Park                   Bar   
30       Mill Island           Pizza Place       Harbor / Marina   
31   Manhattan Beach    Italian Restaurant    Turkish Restaurant   
61      Fulton Ferry                  Park        Scenic Lookout   
62      Vinegar Hill                  Park         Boat or Ferry   
65             Dumbo                  Park   American Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
12         Deli / Bodega             Wine Shop            Playground  
18           Pizza Place             Wine Shop           Coffee Shop  
21    Seafood Restaurant           Art Gallery             Wine Shop  
30                   Gym        Sandwich Place        Hardware Store  
31                  Café        Sandwich Place          Dessert Shop  
61           Coffee Shop   American Restaurant            Playground  
62   American Restaurant             Wine Shop           Art Gallery  
65        Scenic Lookout           Pizza Place           Coffee Shop

#### Cluster 5


In [108]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 4, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
39     Sea Gate                 Beach           Supermarket   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
39      Basketball Court                  Park         Grocery Store

#### Cluster 6

In [109]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 5, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
45  Bergen Beach    Italian Restaurant         Deli / Bodega   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
45               Stables   American Restaurant           Supermarket

#### Cluster 7

In [110]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] ==6, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
14    Brownsville        Discount Store                Pizza Place   
25  Cypress Hills           Pizza Place  Latin American Restaurant   
26  East New York    Chinese Restaurant                Pizza Place   
44      City Line           Pizza Place        Fried Chicken Joint   
58       New Lots  Fast Food Restaurant                Pizza Place   
67  Highland Park           Pizza Place  Latin American Restaurant   

   3rd Most Common Venue      4th Most Common Venue 5th Most Common Venue  
14           Supermarket             Sandwich Place     Mobile Phone Shop  
25  Fast Food Restaurant              Grocery Store            Donut Shop  
26           Supermarket              Metro Station              Pharmacy  
44  Fast Food Restaurant  Latin American Restaurant            Donut Shop  
58         Metro Station              Deli / Bodega  Caribbean Restaurant  
67  Fast Food Restaurant             Ice Cream Shop            Donut Shop

### Cluster 8

In [112]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 7, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood         1st Most Common Venue 2nd Most Common Venue  \
32  Coney Island  Theme Park Ride / Attraction            Theme Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
32              Pharmacy           Pizza Place                 Beach

### Conclusion

So from examing the above clusters we can predict the neighbourhood where food places should be opened. For example opening a resturant  at cluster 5 in the neighbourhood of Sea Beach would be appropiate since there is no popular resturants nearby.

Similiarly a bakery can be opened at cluster 7 since the top 5 venues in all of its neighbourhoods do not have a bakery.

This notebook is the project for the Capstone Project on **Coursera**.